In [3]:
import json
import pickle

def read_json_from_local(file_path: str) -> dict:
  with open(file_path, "r") as json_file:
      j = json.load(json_file)
  return j

def read_pickle_from_local(file_path: str):
  with open(file_path, "rb") as json_file:
      p = pickle.load(json_file)
  return p

def find_all_source_fragment_ids(data, total_data, results):
    if isinstance(data, dict):
        for key, value in data.items():
            if key == "sourceFragmentIds":
                print(data)
                results += value
                data.get('children').update(total_data[str(value[0])])
            else:
                find_all_source_fragment_ids(value, total_data, results)
    elif isinstance(data, list):
        for item in data:
            find_all_source_fragment_ids(item, total_data, results)

In [17]:
j = read_json_from_local('./test/data/complex_trino_plan.txt')
j

{'0': {'id': '35',
  'name': 'Output',
  'descriptor': {'columnNames': '[acctbal, name, name, partkey, mfgr, address, phone, comment]'},
  'outputs': [{'symbol': 'acctbal', 'type': 'double'},
   {'symbol': 'name_1', 'type': 'varchar(25)'},
   {'symbol': 'name_9', 'type': 'varchar(25)'},
   {'symbol': 'partkey_4', 'type': 'bigint'},
   {'symbol': 'mfgr', 'type': 'varchar(25)'},
   {'symbol': 'address', 'type': 'varchar(40)'},
   {'symbol': 'phone', 'type': 'varchar(15)'},
   {'symbol': 'comment_2', 'type': 'varchar(101)'}],
  'details': ['name := name_1',
   'name := name_9',
   'partkey := partkey_4',
   'comment := comment_2'],
  'estimates': [{'outputRowCount': 100.0,
    'outputSizeInBytes': 34800.0,
    'cpuCost': 0.0,
    'memoryCost': 0.0,
    'networkCost': 0.0}],
  'children': [{'id': '1619',
    'name': 'TopN',
    'descriptor': {'count': '100',
     'orderBy': '[acctbal DESC NULLS LAST, name_9 ASC NULLS LAST, name_1 ASC NULLS LAST, partkey_4 ASC NULLS LAST]'},
    'outputs': 

In [18]:
parsed_json = j;
parsed_json.keys()

dict_keys(['0', '1', '2', '3', '4', '5', '6', '7', '8', '9', '10', '11'])

In [21]:

def merge_to_parent(childrens, root, delete_items):
  for child in childrens:
    if child.get('descriptor') and child.get('descriptor').get('sourceFragmentIds'):
      l = list()
      ids = json.loads(child.get('descriptor').get('sourceFragmentIds'))
      for id in ids:
        print(f'id: {id}')
        l.append(root.get(str(id)))
        delete_items.append(str(id))
      child['children'] = list(filter(None, l))
    else:
      merge_to_parent(child['children'], root, delete_items)

def convert_to_nested_childrens(root) -> dict:
  delete_items = []
  trees = []

  for k, v in root.items():
    merge_to_parent(v.get('children'), root, delete_items)  

  # for d in delete_items:
  #   if root.get(d):
  #     del(root[d])
  
  trees = list(root.values())[0]
  print(len(trees), trees)

  if len(trees) > 0:
    return trees[0]
  else:
    return None
  
result = convert_to_nested_childrens(parsed_json)
print(json.dumps(result))

id: 1
id: 2
id: 6
id: 11
id: 3
id: 4
id: 5
id: 7
id: 8
id: 9
id: 10
12 [{'id': '35', 'name': 'Output', 'descriptor': {'columnNames': '[acctbal, name, name, partkey, mfgr, address, phone, comment]'}, 'outputs': [{'symbol': 'acctbal', 'type': 'double'}, {'symbol': 'name_1', 'type': 'varchar(25)'}, {'symbol': 'name_9', 'type': 'varchar(25)'}, {'symbol': 'partkey_4', 'type': 'bigint'}, {'symbol': 'mfgr', 'type': 'varchar(25)'}, {'symbol': 'address', 'type': 'varchar(40)'}, {'symbol': 'phone', 'type': 'varchar(15)'}, {'symbol': 'comment_2', 'type': 'varchar(101)'}], 'details': ['name := name_1', 'name := name_9', 'partkey := partkey_4', 'comment := comment_2'], 'estimates': [{'outputRowCount': 100.0, 'outputSizeInBytes': 34800.0, 'cpuCost': 0.0, 'memoryCost': 0.0, 'networkCost': 0.0}], 'children': [{'id': '1619', 'name': 'TopN', 'descriptor': {'count': '100', 'orderBy': '[acctbal DESC NULLS LAST, name_9 ASC NULLS LAST, name_1 ASC NULLS LAST, partkey_4 ASC NULLS LAST]'}, 'outputs': [{'symbol

In [23]:
for (i, item) in enumerate(v):
  print(i, item)

0 {'id': '13', 'name': 'Output', 'descriptor': {'columnNames': '[returnflag, linestatus, sum_qty, sum_base_price, sum_disc_price, sum_charge, avg_qty, avg_price, avg_disc, count_order]'}, 'outputs': [{'symbol': 'returnflag', 'type': 'varchar(1)'}, {'symbol': 'linestatus', 'type': 'varchar(1)'}, {'symbol': 'sum', 'type': 'double'}, {'symbol': 'sum_1', 'type': 'double'}, {'symbol': 'sum_2', 'type': 'double'}, {'symbol': 'sum_3', 'type': 'double'}, {'symbol': 'avg', 'type': 'double'}, {'symbol': 'avg_4', 'type': 'double'}, {'symbol': 'avg_5', 'type': 'double'}, {'symbol': 'count', 'type': 'bigint'}], 'details': ['sum_qty := sum', 'sum_base_price := sum_1', 'sum_disc_price := sum_2', 'sum_charge := sum_3', 'avg_qty := avg', 'avg_price := avg_4', 'avg_disc := avg_5', 'count_order := count'], 'estimates': [{'outputRowCount': 'NaN', 'outputSizeInBytes': 'NaN', 'cpuCost': 0.0, 'memoryCost': 0.0, 'networkCost': 0.0}], 'children': [{'id': '307', 'name': 'RemoteMerge', 'descriptor': {'sourceFragm

In [26]:
def pop(stage_id, l) -> dict:
  for (i, item) in enumerate(l):
    if item['id'] == stage_id:
      return l.pop(i)
  return None

In [32]:
v.pop(2)

{'id': '438',
 'name': 'Project',
 'descriptor': {},
 'outputs': [{'symbol': 'returnflag', 'type': 'varchar(1)'},
  {'symbol': 'linestatus', 'type': 'varchar(1)'},
  {'symbol': 'avg', 'type': 'double'},
  {'symbol': 'sum_3', 'type': 'double'},
  {'symbol': 'sum_2', 'type': 'double'},
  {'symbol': 'sum_1', 'type': 'double'},
  {'symbol': 'avg_5', 'type': 'double'},
  {'symbol': 'count', 'type': 'bigint'},
  {'symbol': 'avg_4', 'type': 'double'},
  {'symbol': 'sum', 'type': 'double'}],
 'details': [],
 'estimates': [{'outputRowCount': 'NaN',
   'outputSizeInBytes': 'NaN',
   'cpuCost': 'NaN',
   'memoryCost': 0.0,
   'networkCost': 0.0}],
 'children': [{'id': '5',
   'name': 'Aggregate',
   'descriptor': {'type': 'FINAL',
    'keys': '[returnflag, linestatus]',
    'hash': '[$hashvalue]'},
   'outputs': [{'symbol': 'returnflag', 'type': 'varchar(1)'},
    {'symbol': 'linestatus', 'type': 'varchar(1)'},
    {'symbol': '$hashvalue', 'type': 'bigint'},
    {'symbol': 'avg', 'type': 'double'

In [116]:
read_pickle_from_local('/Users/songgane/Dev/src/github/query-optimizer/Auto-Steer/nn/data/trino_data/x_train')

[{'id': '26',
  'name': 'Output',
  'descriptor': {'columnNames': '[brand, type, size, supplier_cnt]'},
  'outputs': [{'symbol': 'brand', 'type': 'varchar(10)'},
   {'symbol': 'type', 'type': 'varchar(25)'},
   {'symbol': 'size', 'type': 'integer'},
   {'symbol': 'count', 'type': 'bigint'}],
  'details': ['supplier_cnt := count'],
  'estimates': [{'outputRowCount': 'NaN',
    'outputSizeInBytes': 'NaN',
    'cpuCost': 0.0,
    'memoryCost': 0.0,
    'networkCost': 0.0}],
  'children': [{'id': '955',
    'name': 'RemoteMerge',
    'descriptor': {'sourceFragmentIds': '[1]'},
    'outputs': [{'symbol': 'brand', 'type': 'varchar(10)'},
     {'symbol': 'type', 'type': 'varchar(25)'},
     {'symbol': 'size', 'type': 'integer'},
     {'symbol': 'count', 'type': 'bigint'}],
    'details': [],
    'estimates': [],
    'children': [{'id': '1168',
      'name': 'LocalMerge',
      'descriptor': {'orderBy': '[count DESC NULLS LAST, brand ASC NULLS LAST, type ASC NULLS LAST, size ASC NULLS LAST]'},

In [119]:
read_pickle_from_local('/Users/songgane/Dev/src/github/query-optimizer/Auto-Steer/nn/data/trino_data/y_train')

[233000.0,
 166500.0,
 275500.0,
 273000.0,
 275000.0,
 295000.0,
 196500.0,
 234000.0,
 170500.0,
 38500.0,
 40000.0,
 40000.0,
 38000.0,
 36000.0,
 36500.0,
 35000.0,
 37000.0,
 51000.0,
 36000.0,
 34000.0,
 36500.0,
 34000.0,
 36000.0,
 33000.0,
 57500.0,
 54000.0,
 57000.0,
 62000.0,
 72500.0,
 59500.0,
 56000.0,
 55500.0,
 42500.0,
 42000.0,
 45000.0,
 47000.0,
 44500.0,
 48000.0,
 44500.0,
 139500.0,
 151500.0,
 139000.0,
 136500.0,
 146500.0,
 131500.0,
 117500.0,
 123000.0,
 129500.0,
 117000.0,
 136500.0,
 125000.0,
 119000.0,
 107500.0,
 120000.0,
 117500.0,
 107000.0,
 108500.0,
 52500.0,
 40500.0,
 49000.0,
 67000.0,
 51000.0,
 51500.0,
 50000.0,
 51000.0,
 41000.0,
 40500.0,
 40500.0,
 39500.0,
 51500.0,
 51000.0,
 47000.0,
 51000.0,
 48500.0,
 42000.0,
 40000.0,
 38500.0,
 46500.0,
 41500.0,
 48000.0,
 61000.0,
 59500.0,
 63500.0,
 70000.0,
 62000.0,
 64000.0,
 61000.0,
 264500.0,
 287500.0,
 215500.0,
 221000.0,
 221500.0,
 259000.0,
 229000.0,
 218000.0,
 274000.0,
 220

In [120]:
read_pickle_from_local('/Users/songgane/Dev/src/github/query-optimizer/Auto-Steer/nn/model/trino_model/channels')

19

In [121]:
read_pickle_from_local('/Users/songgane/Dev/src/github/query-optimizer/Auto-Steer/nn/model/trino_model/x_transform')

ModuleNotFoundError: No module named 'inference'